In [13]:
import os
from collections import defaultdict

import matplotlib.pyplot as plt
import pandas as pd
import plotly.graph_objects as go

In [14]:
def print_tree(directory, prefix="", depth=0, max_depth=None, extensions=None):
    if max_depth is not None and depth >= max_depth:
        return

    entries = sorted(os.listdir(directory))
    num_entries = len(entries)

    for i, entry in enumerate(entries):
        path = os.path.join(directory, entry)
        is_last = (i == num_entries - 1)

        # 拡張子フィルタリング（ディレクトリは常に表示）
        if os.path.isfile(path) and extensions is not None:
            if not any(entry.endswith(ext) for ext in extensions):
                continue

        print(prefix + ("└── " if is_last else "├── ") + entry)

        if os.path.isdir(path):
            new_prefix = prefix + ("    " if is_last else "│   ")
            print_tree(path, new_prefix, depth + 1, max_depth, extensions)

# 獲得関数の確率分布

```
structure_dict_acqf = {
    "constrained": {
        "warcraft-1": ["n", "t1", "t2"],
        "warcraft-2": ["n", "t1", "t2"],
        "ackley": ["n", "t1", "t2"]
    },
    "unconstrained": {
        "warcraft-1": ["n", "t1", "t2"],
        "warcraft-2": ["n", "t1", "t2"],
        "ackley": ["n", "t1", "t2"]
    }
}
```

In [15]:
import os
from collections import defaultdict


def get_filtered_csv_files(directory, max_depth=2, exclude_keyword="loss_history"):
    """
    指定したディレクトリ内の `.csv` ファイルのうち、
    ファイル名に `exclude_keyword` を含まないものの絶対パスを取得する。

    Parameters:
    - directory (str): 探索するディレクトリ
    - max_depth (int): 探索する最大の階層
    - exclude_keyword (str): 除外するキーワード
    
    Returns:
    - List[str]: 条件を満たすファイルの絶対パスリスト
    """
    filtered_files = []
    
    def search_files(current_dir, depth):
        if depth < 0:
            return
        
        try:
            entries = sorted(os.listdir(current_dir))
        except PermissionError:
            return  # 権限エラーが発生した場合はスキップ
        
        for entry in entries:
            path = os.path.join(current_dir, entry)
            if os.path.isdir(path):
                search_files(path, depth - 1)
            elif entry.endswith(".csv") and exclude_keyword not in entry:
                filtered_files.append(os.path.abspath(path))
    
    search_files(directory, max_depth)
    return filtered_files

def categorize_files_by_date(file_paths):
    """
    ファイルパスリストを、日付ディレクトリごとに分類する。

    Parameters:
    - file_paths (List[str]): 絶対パスのリスト

    Returns:
    - dict: { 日付ディレクトリ: [ファイルパスリスト] } の辞書
    """
    categorized_files = defaultdict(list)

    for file_path in file_paths:
        # ファイルの親ディレクトリを取得
        parent_dir = os.path.basename(os.path.dirname(file_path))
        
        # 日付ディレクトリとして分類
        categorized_files[parent_dir].append(file_path)
    
    return dict(categorized_files)


target_file_path_list = get_filtered_csv_files("results_acqf_dist")
categorized_file_paths_dict = categorize_files_by_date(target_file_path_list)

structure_dict_acqf = {
    "constrained": {
        "warcraft-1": {"n": [], "t1": [], "t2": []},
        "warcraft-2": {"n": [], "t1": [], "t2": []},
        "ackley": {"n": [], "t1": [], "t2": []},
    },
    "unconstrained": {
        "warcraft-1": {"n": [], "t1": [], "t2": []},
        "warcraft-2": {"n": [], "t1": [], "t2": []},
        "ackley": {"n": [], "t1": [], "t2": []},
    }
}


gen_categorized_file_paths_dict = iter(categorized_file_paths_dict.values())

for const in ["constrained", "unconstrained"]:
    for problem in ["warcraft-1", "warcraft-2", "ackley"]:
        for method in ["n", "t1", "t2"]:
            structure_dict_acqf[const][problem][method] = next(gen_categorized_file_paths_dict)

structure_dict_acqf

{'constrained': {'warcraft-1': {'n': ['/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed0.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed1.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed2.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed3.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed4.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed5.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed6.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed7.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf

In [16]:
import pandas as pd
import numpy as np
from tabulate import tabulate

def load_and_process_data_for_table(files):
    """Load CSV files and calculate statistics"""
    all_best_values = []
    first_best_trial = []
    constraints_count = []
    durations = []
    min_length = float('inf')

    # Find minimum length for truncation
    for file in files:
        df = pd.read_csv(file)
        min_length = min(min_length, len(df['best_value']))

    # Collect statistics
    for file in files:
        df = pd.read_csv(file).iloc[:min_length]  # Trim to min length

        all_best_values.append(df['best_value'].values)
        
        # Find the first occurrence of the minimum value
        min_value = df['best_value'].min()
        first_best_trial.append(df[df['best_value'] == min_value].index[0])

        # print(f"first best trial: {df[df['best_value'] == min_value].index[0]}")

        constraints_count.append(df['constraint'].sum() / min_length)  # Count True occurrences
        durations.append(pd.to_timedelta(df['duration']).dt.total_seconds().sum())  # Convert to cumulative seconds

    # Convert to numpy arrays
    all_best_values = np.array(all_best_values)
    first_best_trial = np.array(first_best_trial)
    constraints_count = np.array(constraints_count)
    durations = np.array(durations)

    # Compute statistics
    mean_best = np.mean(all_best_values, axis=0)[-1]  # Last iteration mean
    std_best = np.std(all_best_values, axis=0)[-1]   # Last iteration std dev
    mean_duration = np.mean(durations)
    std_duration = np.std(durations)
    mean_best_value_found = np.mean(first_best_trial)
    std_best_value_found = np.std(first_best_trial)
    mean_constraints = np.mean(constraints_count)
    std_constraints = np.std(constraints_count)

    return {
        "mean_best_value": mean_best,
        "std_best_value": std_best,
        "mean_duration": mean_duration,
        "std_duration": std_duration,
        "mean_best_value_found": mean_best_value_found,
        "std_best_value_found": std_best_value_found,
        "mean_constraints": mean_constraints,
        "std_constraints": std_constraints
    }

def create_comparison_table(data_dict, constraint_type):
    """Generate a statistical comparison table for different methods."""
    table_data_dict = {}
    
    for task_key, methods in data_dict.items():
        print(f"Task: {task_key} ({constraint_type})")

        table_data = []

        for method, files in methods.items():
            if not files:
                continue  # Skip if empty

            stats = load_and_process_data_for_table(files)

            table_data.append([
                method,
                f"{stats['mean_best_value']:.4f} ± {stats['std_best_value']:.4f}",
                f"{stats['mean_duration']:.2f} ± {stats['std_duration']:.2f} sec",
                f"{stats['mean_best_value_found']:.2f} ± {stats['std_best_value_found']:.2f} trials",
                f"{stats['mean_constraints']:.2f} ± {stats['std_constraints']:.2f}"
            ])

        # Print formatted table
        headers = ["Method", "Best Value (Mean ± Std)", "Duration (Mean ± Std)", "Best Value Found (Trial)", "Constraints"]

        table_data_dict[task_key] = tabulate(table_data, headers=headers, tablefmt="grid")

    return table_data_dict

In [17]:
# Execute the table generation
table_data_dict = create_comparison_table(data_dict=structure_dict_acqf['constrained'], constraint_type='Constrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")


table_data_dict = create_comparison_table(data_dict=structure_dict_acqf['unconstrained'], constraint_type='unonstrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")

Task: warcraft-1 (Constrained)


Task: warcraft-2 (Constrained)
Task: ackley (Constrained)

warcraft-1
+----------+---------------------------+-------------------------+----------------------------+---------------+
| Method   | Best Value (Mean ± Std)   | Duration (Mean ± Std)   | Best Value Found (Trial)   | Constraints   |
+==========+===========================+=========================+============================+===============+
| n        | 0.5000 ± 0.0000           | 191.11 ± 4.87 sec       | 32.40 ± 14.57 trials       | 0.59 ± 0.01   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| t1       | 0.5000 ± 0.0000           | 192.49 ± 3.34 sec       | 34.10 ± 12.34 trials       | 0.15 ± 0.01   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| t2       | 0.5196 ± 0.0589           | 194.43 ± 6.09 sec       | 120.20 ± 177.02 trials     | 0.12 ± 0.02   |
+----------+----------------------

In [18]:
table_data_dict['warcraft-1']

'+----------+---------------------------+-------------------------+----------------------------+---------------+\n| Method   | Best Value (Mean ± Std)   | Duration (Mean ± Std)   | Best Value Found (Trial)   | Constraints   |\n+==========+===========================+=========================+============================+===============+\n| n        | 0.5000 ± 0.0000           | 413.32 ± 106.48 sec     | 230.10 ± 27.80 trials      | 0.19 ± 0.01   |\n+----------+---------------------------+-------------------------+----------------------------+---------------+\n| t1       | 0.5000 ± 0.0000           | 418.53 ± 102.43 sec     | 226.70 ± 22.45 trials      | 0.11 ± 0.02   |\n+----------+---------------------------+-------------------------+----------------------------+---------------+\n| t2       | 0.5000 ± 0.0000           | 397.78 ± 109.34 sec     | 232.00 ± 48.49 trials      | 0.06 ± 0.01   |\n+----------+---------------------------+-------------------------+----------------------------+

In [7]:
import json

data = structure_dict_acqf

# JSON ファイルに保存
with open("data.json", "w", encoding="utf-8") as f:
    json.dump(data, f, ensure_ascii=False, indent=4)  # 日本語対応 & 整形


In [8]:
structure_dict_acqf

{'constrained': {'warcraft-1': {'n': ['/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed0.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed1.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed2.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed3.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed4.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed5.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed6.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf_dist/2025-01-29_16-39-51/warcraft_map1_train_n_seed7.csv',
    '/work/keisuke-o/ws/constrained_BO_v3/results_acqf

In [19]:
import plotly.graph_objects as go
import numpy as np
import plotly.colors

def create_comparison_plot(data_dict, constraint_type, error_bar_interval=10, n_sigma=2, expected_length=500):
    """Create comparison plot for constrained or unconstrained tasks"""
    for task_key, methods in data_dict.items():
        fig = go.Figure()
        colors = plotly.colors.qualitative.Plotly

        for i, (method, files) in enumerate(methods.items()):
            if not files:
                continue  # 空のリストはスキップ
            
            mean, std, length = load_and_process_data(files)
            x = np.arange(1, length + 1)  # 1から始める（対数スケールに適応）
            
            # 平均値の線（マーカーなし）
            fig.add_trace(go.Scatter(
                x=x,
                y=mean,
                mode='lines',
                name=f"{task_key} - {method}",
                line=dict(color=colors[i], width=2),
                opacity=1,
                showlegend=True
            ))

            # 信頼区間のエラーバー（一定間隔）
            r, g, b = plotly.colors.hex_to_rgb(colors[i])  # RGB取得
            
            error_indices = np.arange(0, length, error_bar_interval)
            fig.add_trace(go.Scatter(
                x=x[error_indices],
                y=mean[error_indices],
                mode='markers',
                marker=dict(
                    symbol='line-ns',
                    color=f"rgba({r},{g},{b},0.3)",
                ),
                error_y=dict(
                    type='data',
                    array=std[error_indices] * n_sigma,
                    visible=True
                ),
                showlegend=False
            ))

            # 最小値のマーカー
            min_index = np.argmin(mean)
            fig.add_trace(go.Scatter(
                x=[x[min_index]],
                y=[mean[min_index]],
                name=f"Min Point ({task_key} - {method})",
                mode='markers',
                marker=dict(
                    size=8,
                    color=colors[i],
                ),
                showlegend=True
            ))

            # 途中終了チェック
            if length < expected_length:
                fig.add_trace(go.Scatter(
                    x=[x[-1]],
                    y=[mean[-1]],
                    name=f"Early Stop ({task_key} - {method})",
                    mode='markers',
                    marker=dict(
                        symbol='x',
                        size=12,
                        color=colors[i],
                    ),
                    showlegend=True
                ))

        # 縦軸の範囲設定
        y_range = [0, 20] if task_key.lower() == "ackley" else [0, 2] if task_key.lower() == "warcraft" else None

        fig.update_layout(
            title=f'Comparison of Algorithms on {task_key} ({constraint_type})',
            xaxis_title='Iteration',
            yaxis_title='Best Value',
            template='plotly_white',
            width=8.5 * 37.8,  # 8.5cm を pixel に変換
            height=400,  # 高さは適宜調整
            yaxis=dict(range=y_range) if y_range else {},
        )
        
        fig.show()

# 可視化の実行
create_comparison_plot(data_dict=structure_dict_acqf['constrained'], constraint_type='Constrained')
create_comparison_plot(data_dict=structure_dict_acqf['unconstrained'], constraint_type='Unconstrained')


# ランクとモデルの選択

```
structure_dict_rank = {
    "rank-2": {
        "constrained": {
            "warcraft-1": ["cp", "train", "ring"],
            "warcraft-2": ["cp", "train", "ring"],
            "ackley": ["cp", "train", "ring"]
        },
        "unconstrained": {
            "warcraft-1": ["cp", "train", "ring"],
            "warcraft-2": ["cp", "train", "ring"],
            "ackley": ["cp", "train", "ring"]
        }
    },
    "rank-3": {
        ...
}
```

In [10]:
target_file_path_list = []

for target_dir in [
    "results_tf_method_2",
    "results_tf_method_3",
    "results_tf_method_4",
    "results_tf_method_5",
    "results_tf_method_6",
]:
    temp_file_path_list = get_filtered_csv_files(target_dir)
    target_file_path_list.extend(temp_file_path_list)

categorized_file_paths_dict = categorize_files_by_date(target_file_path_list)

structure_dict_rank = {
    "rank-2": {
        "constrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        },
        "unconstrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        }
    },
    "rank-3": {
        "constrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        },
        "unconstrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        }
    },
    "rank-4": {
        "constrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        },
        "unconstrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        }
    },
    "rank-5": {
        "constrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        },
        "unconstrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        }
    },
    "rank-6": {
        "constrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        },
        "unconstrained": {
            "warcraft-1": {"cp": [], "train": [], "ring": []},
            "warcraft-2": {"cp": [], "train": [], "ring": []},
            "ackley": {"cp": [], "train": [], "ring": []},
        }
    },
}

gen_categorized_file_paths_dict = iter(categorized_file_paths_dict.values())

for rank in ["rank-2", "rank-3", "rank-4", "rank-5", "rank-6"]:
    for const in ["constrained", "unconstrained"]:
        for problem in ["warcraft-1", "warcraft-2", "ackley"]:
            for method in ["cp", "train", "ring"]:
                structure_dict_rank[rank][const][problem][method] = next(gen_categorized_file_paths_dict)

structure_dict_rank

{'rank-2': {'constrained': {'warcraft-1': {'cp': ['/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed0.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed1.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed2.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed3.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed4.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed5.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed6.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed7.csv',
     '/work/keisuke-o/ws/constrained_BO_v3/

In [11]:
def extract_only(data, method="cp"):
    """ Recursively extract all 'cp' values from the nested dictionary. """
    result = {}

    if isinstance(data, dict):
        for key, value in data.items():
            if key == method:
                return value  # If 'cp' is found, return its value (list of paths)
            else:
                nested_result = extract_only(value, method=method)
                if nested_result:
                    result[key] = nested_result

    return result if result else None

def restructure_data(data):
    """
    Restructure the dictionary so that 'rank' becomes the innermost key.
    """
    new_structure = defaultdict(lambda: defaultdict(lambda: defaultdict(list)))
    
    for rank, conditions in data.items():
        for condition, maps in conditions.items():
            for map_name, file_paths in maps.items():
                new_structure[condition][map_name][rank] = file_paths
    
    return dict(new_structure)

# ここで `data` は元の辞書 (ユーザーが提供したもの)
cp_only_data = extract_only(structure_dict_rank, method="cp")
target_data_dict = restructure_data(cp_only_data)

target_data_dict

{'constrained': defaultdict(<function __main__.restructure_data.<locals>.<lambda>.<locals>.<lambda>()>,
             {'warcraft-1': defaultdict(list,
                          {'rank-2': ['/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed0.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed1.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed2.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed3.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed4.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-20/warcraft_map1_cp_n_seed5.csv',
                  

In [12]:
import pandas as pd
import numpy as np
from tabulate import tabulate

def load_and_process_data_for_table(files):
    """Load CSV files and calculate statistics"""
    all_best_values = []
    first_best_trial = []
    constraints_count = []
    durations = []
    min_length = float('inf')

    # Find minimum length for truncation
    for file in files:
        df = pd.read_csv(file)
        min_length = min(min_length, len(df['best_value']))

    # Collect statistics
    for file in files:
        df = pd.read_csv(file).iloc[:min_length]  # Trim to min length

        all_best_values.append(df['best_value'].values)
        
        # Find the first occurrence of the minimum value
        min_value = df['best_value'].min()
        first_best_trial.append(df[df['best_value'] == min_value].index[0])

        # print(f"first best trial: {df[df['best_value'] == min_value].index[0]}")

        constraints_count.append(df['constraint'].sum() / min_length)  # Count True occurrences
        durations.append(pd.to_timedelta(df['duration']).dt.total_seconds().sum())  # Convert to cumulative seconds

    # Convert to numpy arrays
    all_best_values = np.array(all_best_values)
    first_best_trial = np.array(first_best_trial)
    constraints_count = np.array(constraints_count)
    durations = np.array(durations)

    # Compute statistics
    mean_best = np.mean(all_best_values, axis=0)[-1]  # Last iteration mean
    std_best = np.std(all_best_values, axis=0)[-1]   # Last iteration std dev
    mean_duration = np.mean(durations)
    std_duration = np.std(durations)
    mean_best_value_found = np.mean(first_best_trial)
    std_best_value_found = np.std(first_best_trial)
    mean_constraints = np.mean(constraints_count)
    std_constraints = np.std(constraints_count)

    return {
        "mean_best_value": mean_best,
        "std_best_value": std_best,
        "mean_duration": mean_duration,
        "std_duration": std_duration,
        "mean_best_value_found": mean_best_value_found,
        "std_best_value_found": std_best_value_found,
        "mean_constraints": mean_constraints,
        "std_constraints": std_constraints
    }

def create_comparison_table(data_dict, constraint_type):
    """Generate a statistical comparison table for different methods."""
    table_data_dict = {}
    
    for task_key, methods in data_dict.items():
        print(f"Task: {task_key} ({constraint_type})")

        table_data = []

        for method, files in methods.items():
            if not files:
                continue  # Skip if empty

            stats = load_and_process_data_for_table(files)

            table_data.append([
                method,
                f"{stats['mean_best_value']:.4f} ± {stats['std_best_value']:.4f}",
                f"{stats['mean_duration']:.2f} ± {stats['std_duration']:.2f} sec",
                f"{stats['mean_best_value_found']:.2f} ± {stats['std_best_value_found']:.2f} trials",
                f"{stats['mean_constraints']:.2f} ± {stats['std_constraints']:.2f}"
            ])

        # Print formatted table
        headers = ["Method", "Best Value (Mean ± Std)", "Duration (Mean ± Std)", "Best Value Found (Trial)", "Constraints"]

        table_data_dict[task_key] = tabulate(table_data, headers=headers, tablefmt="grid")

    return table_data_dict

# Execute the table generation
only_data = extract_only(structure_dict_rank, method="cp")
target_data_dict = restructure_data(only_data)
table_data_dict = create_comparison_table(data_dict=target_data_dict['constrained'], constraint_type='Constrained')


Task: warcraft-1 (Constrained)
Task: warcraft-2 (Constrained)
Task: ackley (Constrained)


In [13]:
# Execute the table generation
only_data = extract_only(structure_dict_rank, method="cp")
target_data_dict = restructure_data(only_data)

table_data_dict = create_comparison_table(data_dict=target_data_dict['constrained'], constraint_type='Constrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")


table_data_dict = create_comparison_table(data_dict=target_data_dict['unconstrained'], constraint_type='unonstrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")

Task: warcraft-1 (Constrained)
Task: warcraft-2 (Constrained)
Task: ackley (Constrained)

warcraft-1
+----------+---------------------------+-------------------------+----------------------------+---------------+
| Method   | Best Value (Mean ± Std)   | Duration (Mean ± Std)   | Best Value Found (Trial)   | Constraints   |
+==========+===========================+=========================+============================+===============+
| rank-2   | 0.5000 ± 0.0000           | 180.73 ± 7.66 sec       | 36.40 ± 30.57 trials       | 0.59 ± 0.03   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| rank-3   | 0.5000 ± 0.0000           | 202.09 ± 10.86 sec      | 33.90 ± 24.70 trials       | 0.50 ± 0.03   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| rank-4   | 0.5000 ± 0.0000           | 216.05 ± 5.50 sec       | 34.80 ± 17.16 trials       | 0.48 ± 0.02   |
+--

In [14]:
# Execute the table generation
only_data = extract_only(structure_dict_rank, method="train")
target_data_dict = restructure_data(only_data)

table_data_dict = create_comparison_table(data_dict=target_data_dict['constrained'], constraint_type='Constrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")


table_data_dict = create_comparison_table(data_dict=target_data_dict['unconstrained'], constraint_type='unonstrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")

Task: warcraft-1 (Constrained)
Task: warcraft-2 (Constrained)
Task: ackley (Constrained)

warcraft-1
+----------+---------------------------+-------------------------+----------------------------+---------------+
| Method   | Best Value (Mean ± Std)   | Duration (Mean ± Std)   | Best Value Found (Trial)   | Constraints   |
+==========+===========================+=========================+============================+===============+
| rank-2   | 0.5000 ± 0.0000           | 185.36 ± 3.31 sec       | 33.20 ± 16.41 trials       | 0.60 ± 0.00   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| rank-3   | 0.5000 ± 0.0000           | 193.86 ± 11.49 sec      | 32.40 ± 14.57 trials       | 0.59 ± 0.01   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| rank-4   | 0.5000 ± 0.0000           | 190.96 ± 7.84 sec       | 34.40 ± 23.22 trials       | 0.59 ± 0.01   |
+--

In [15]:
# Execute the table generation
only_data = extract_only(structure_dict_rank, method="ring")
target_data_dict = restructure_data(only_data)

table_data_dict = create_comparison_table(data_dict=target_data_dict['constrained'], constraint_type='Constrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")


table_data_dict = create_comparison_table(data_dict=target_data_dict['unconstrained'], constraint_type='unonstrained')

print()
for key, value in table_data_dict.items():
    print(key)
    print(value)
    print("\n")

Task: warcraft-1 (Constrained)
Task: warcraft-2 (Constrained)
Task: ackley (Constrained)

warcraft-1
+----------+---------------------------+-------------------------+----------------------------+---------------+
| Method   | Best Value (Mean ± Std)   | Duration (Mean ± Std)   | Best Value Found (Trial)   | Constraints   |
+==========+===========================+=========================+============================+===============+
| rank-2   | 0.5000 ± 0.0000           | 189.64 ± 5.94 sec       | 27.20 ± 15.26 trials       | 0.60 ± 0.00   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| rank-3   | 0.5000 ± 0.0000           | 194.41 ± 6.01 sec       | 30.90 ± 17.61 trials       | 0.60 ± 0.00   |
+----------+---------------------------+-------------------------+----------------------------+---------------+
| rank-4   | 0.5000 ± 0.0000           | 197.80 ± 12.54 sec      | 32.70 ± 14.04 trials       | 0.60 ± 0.00   |
+--

In [16]:
# import json

# data = target_data_dict

# # JSON ファイルに保存
# with open("data.json", "w", encoding="utf-8") as f:
#     json.dump(data, f, ensure_ascii=False, indent=4)  # 日本語対応 & 整形


In [17]:
target_data_dict

{'constrained': defaultdict(<function __main__.restructure_data.<locals>.<lambda>.<locals>.<lambda>()>,
             {'warcraft-1': defaultdict(list,
                          {'rank-2': ['/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-23/warcraft_map1_ring_n_seed0.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-23/warcraft_map1_ring_n_seed1.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-23/warcraft_map1_ring_n_seed2.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-23/warcraft_map1_ring_n_seed3.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-23/warcraft_map1_ring_n_seed4.csv',
                            '/work/keisuke-o/ws/constrained_BO_v3/results_tf_method_2/2025-01-29_17-04-23/warcraft_map1_ring_n_seed5.csv',
      

In [18]:
target_data_dict.keys(), target_data_dict['constrained'].keys(), target_data_dict['constrained']['warcraft-1'].keys()

(dict_keys(['constrained', 'unconstrained']),
 dict_keys(['warcraft-1', 'warcraft-2', 'ackley']),
 dict_keys(['rank-2', 'rank-3', 'rank-4', 'rank-5', 'rank-6']))

In [19]:
# 可視化の実行
create_comparison_plot(data_dict=target_data_dict['constrained'], constraint_type='Constrained')
create_comparison_plot(data_dict=target_data_dict['unconstrained'], constraint_type='Unconstrained')

### train

In [20]:
# ここで `data` は元の辞書 (ユーザーが提供したもの)
train_only_data = extract_only(structure_dict_rank, method="train")
target_data_dict = restructure_data(train_only_data)

# 可視化の実行
create_comparison_plot(data_dict=target_data_dict['constrained'], constraint_type='Constrained')
create_comparison_plot(data_dict=target_data_dict['unconstrained'], constraint_type='Unconstrained')

### ring

In [21]:
# ここで `data` は元の辞書 (ユーザーが提供したもの)
ring_only_data = extract_only(structure_dict_rank, method="ring")
target_data_dict = restructure_data(ring_only_data)

# 可視化の実行
create_comparison_plot(data_dict=target_data_dict['constrained'], constraint_type='Constrained')
create_comparison_plot(data_dict=target_data_dict['unconstrained'], constraint_type='Unconstrained')